In [ ]:
from datetime import datetime as dt
from collections import namedtuple
from pathlib import Path

from toargridding.toar_rest_client import AnalysisService
from toargridding.grids import RegularGrid
from toargridding.gridding import get_gridded_toar_data
from toargridding.metadata import TimeSample

In [ ]:
Config = namedtuple("Config", ["grid", "time", "variables", "stats"])

valid_data = Config(
    RegularGrid(1.9, 2.5),
    TimeSample(dt(2014,1,1), dt(2019,12,31), sampling="daily"),
    ["mole_fraction_of_ozone_in_air"],
    ["mean"]# ["dma8epax"], # enable when finished
)
missing_data = Config(
    RegularGrid(1.9, 2.5),
    TimeSample(dt(2000,1,1), dt(2013,12,31), sampling="daily"),
    ["mole_fraction_of_ozone_in_air"],
    ["dma8epax"],
)

configs = {
    "tabish_ansari": valid_data
}

config = configs["tabish_ansari"]
config.grid

In [ ]:
stats_endpoint = "https://toar-data.fz-juelich.de/api/v2/analysis/statistics/"
result_basepath = Path("results")
analysis_service = AnalysisService(stats_endpoint, result_basepath)

for person, config in configs.items():
    datasets, metadatas = get_gridded_toar_data(
        analysis_service=analysis_service,
        grid=config.grid,
        time=config.time,
        variables=config.variables,
        stats=config.stats
    )

    for dataset, metadata in zip(datasets, metadatas):
        dataset.to_netcdf(result_basepath / metadata.get_id())